In [13]:
import pandas as pd
import numpy as np

In [2]:
import datetime

filename = "https://raw.githubusercontent.com/antoinecarme/TimeSeriesData/master/Stat_FR_CommExt/merged/French_Wine_Export_in_Euros_Some_Countries.csv"

French_Wine_Export_in_Euros_DF = pd.read_csv(filename);

lDateColumn = 'Month';
French_Wine_Export_in_Euros_DF[lDateColumn] = French_Wine_Export_in_Euros_DF[lDateColumn].apply(lambda x : datetime.datetime.strptime(str(x), "%Y-%m-%d"))

French_Wine_Export_in_Euros_DF.head(5)

Month  ALSACE_BLANC_BE  ALSACE_BLANC_CA  ALSACE_BLANC_CH  \
0 2012-01-01          1131852           571940           257116   
1 2012-02-01           857289           585556           187917   
2 2012-03-01          1438501           834142           679281   
3 2012-04-01           986602           866221           523202   
4 2012-05-01           991668          1061702           611369   

   ALSACE_BLANC_CN  ALSACE_BLANC_DE  ALSACE_BLANC_GB  ALSACE_BLANC_HK  \
0           140013           357516           344274            51043   
1            89805           505896           424953            80220   
2           103577           583887           352675           102980   
3           203456           515903           403517            52773   
4            80327           767522           627232            78115   

   ALSACE_BLANC_JP  ALSACE_BLANC_NL       ...        RHÔNE_ROUGE_CA  \
0           329883           624695       ...                800628   
1           239242           899144       ...                795356   
2           394945          1093638       ...                873858   
3           260953           874217       ...               1004028   
4           680323           994697       ...               2098300   

   RHÔNE_ROUGE_CH  RHÔNE_ROUGE_CN  RHÔNE_ROUGE_DE  RHÔNE_ROUGE_GB  \
0          650236         1127393          783952         1513332   
1          680567          188827          868576         1277664   
2         1318538          856382          627236         2343448   
3          919493          460815          829432         1861188   
4          632778          239200          934532         2215922   

   RHÔNE_ROUGE_HK  RHÔNE_ROUGE_JP  RHÔNE_ROUGE_NL  RHÔNE_ROUGE_OTHER  \
0          335710          916965          314654              35418   
1          197072          318522          516140              36604   
2          132200          605914          410308              43197   
3          128164          472522          290407              45396   
4          202210          337894          284868              41469   

   RHÔNE_ROUGE_US  
0         1260510  
1         2136484  
2         3264810  
3         2631466  
4         2945175  

[5 rows x 177 columns]

In [3]:
df=pd.read_csv('df_test1M.csv')
df.head()

In [9]:
df.head()

Unnamed: 0                     Date  Duration          Src_IP  Src_pt  \
0           0  2017-08-02 00:00:00.419     0.003  192.168.210.55   44870   
1           1  2017-08-02 00:00:00.421     0.000  192.168.100.11     445   
2           2  2017-08-02 00:00:02.593     0.004  192.168.220.47   55101   
3           3  2017-08-02 00:00:02.859     0.000        10000_34     443   
4           4  2017-08-02 00:00:02.594     0.000  192.168.100.11     445   

           Dst_IP   Dst_pt  Packets  Bytes                  date_hr  \
0  192.168.100.11    445.0        2    174  2017-08-02 00:00:00.000   
1  192.168.210.55  44870.0        1    108  2017-08-02 00:00:00.000   
2  192.168.100.11    445.0        2    174  2017-08-02 00:00:00.000   
3  192.168.210.54  59628.0        1    100  2017-08-02 00:00:00.000   
4  192.168.220.47  55101.0        1    108  2017-08-02 00:00:00.000   

                                  pairs                                pairs2  \
0  ['192.168.100.11', '192.168.210.55']  ('192.168.100.11', '192.168.210.55')   
1  ['192.168.100.11', '192.168.210.55']  ('192.168.100.11', '192.168.210.55')   
2  ['192.168.100.11', '192.168.220.47']  ('192.168.100.11', '192.168.220.47')   
3        ['10000_34', '192.168.210.54']        ('10000_34', '192.168.210.54')   
4  ['192.168.100.11', '192.168.220.47']  ('192.168.100.11', '192.168.220.47')   

   norm_latency  
0        0.0015  
1        0.0000  
2        0.0020  
3        0.0000  
4        0.0000

First, determine how frequently each pair occurs in the entire dataset. Also use the latency (either sum or average) to rank how important this pair is.
Pairs with high frequency and high latency get a 'high' rank and are prioritized for rules to determine where the IP should go on which server.
We will actually only concentrate on the top 20% of pairs, as this will allow us to more effectively create time series. 

Since our time series will be predicting the frequency of each pair in each timestep, and then assigning rules to some percentage of them with the highest frequency, it is not necessary to keep all the pairs for this first step.

In [32]:
pairs_count=(df.groupby('pairs2').agg({'Date':'count', 'norm_latency': 'mean', 'Duration': 'sum', 'Packets':'sum'}).reset_index())

pairs_count.columns=['pairs','frequency', 'avg_norm_latency', 'total_duration', 'total_packets']
pairs_count['norm_latency']=(pairs_count['total_duration']/pairs_count['total_packets'].sum())*100 #sum of all duration time divided by sum of all packets transfered for that pair
pairs_count['latency_rank']=pairs_count['frequency']*pairs_count['norm_latency']#high freq and high latency = high rank
pairs_count=pairs_count.sort_values(by='latency_rank', ascending=False)
pairs_count.head()

pairs  frequency  avg_norm_latency  \
415     ('10008_9', '192.168.210.55')     170422          0.001371   
368    ('10008_33', '192.168.210.55')       1838          0.233090   
342    ('10008_24', '192.168.220.46')        781          0.180194   
10652       ('192.168.220.47', 'DNS')      25205          0.004370   
825    ('10035_14', '192.168.220.51')       3706          0.018636   

       total_duration  total_packets  norm_latency  latency_rank  
415          8594.836        8252391      0.037398   6373.472436  
368         75865.783         533433      0.330110    606.742353  
342         29111.314         199981      0.126670     98.929475  
10652         221.958          47174      0.000966     24.342791  
825           925.981          54890      0.004029     14.932081

In [26]:
df.head()

Unnamed: 0                     Date  Duration          Src_IP  Src_pt  \
0           0  2017-08-02 00:00:00.419     0.003  192.168.210.55   44870   
1           1  2017-08-02 00:00:00.421     0.000  192.168.100.11     445   
2           2  2017-08-02 00:00:02.593     0.004  192.168.220.47   55101   
3           3  2017-08-02 00:00:02.859     0.000        10000_34     443   
4           4  2017-08-02 00:00:02.594     0.000  192.168.100.11     445   

           Dst_IP   Dst_pt  Packets  Bytes                  date_hr  \
0  192.168.100.11    445.0        2    174  2017-08-02 00:00:00.000   
1  192.168.210.55  44870.0        1    108  2017-08-02 00:00:00.000   
2  192.168.100.11    445.0        2    174  2017-08-02 00:00:00.000   
3  192.168.210.54  59628.0        1    100  2017-08-02 00:00:00.000   
4  192.168.220.47  55101.0        1    108  2017-08-02 00:00:00.000   

                                  pairs                                pairs2  \
0  ['192.168.100.11', '192.168.210.55']  ('192.168.100.11', '192.168.210.55')   
1  ['192.168.100.11', '192.168.210.55']  ('192.168.100.11', '192.168.210.55')   
2  ['192.168.100.11', '192.168.220.47']  ('192.168.100.11', '192.168.220.47')   
3        ['10000_34', '192.168.210.54']        ('10000_34', '192.168.210.54')   
4  ['192.168.100.11', '192.168.220.47']  ('192.168.100.11', '192.168.220.47')   

   norm_latency  
0        0.0015  
1        0.0000  
2        0.0020  
3        0.0000  
4        0.0000

In [31]:
#find the 80th percentile and filter out things that are below this rank
np80=np.percentile(pairs_count['latency_rank'], [80])[0]
pairs_count80=pairs_count[pairs_count['latency_rank']>np80]
pairs_count80.tail(6)

pairs  frequency  avg_norm_latency  \
1188    ('10045_17', '192.168.220.46')         70          0.031689   
10124   ('11753_70', '192.168.220.51')         59          0.029386   
105    ('10002_174', '192.168.210.57')         70          0.043185   
2818    ('10088_53', '192.168.210.55')         64          0.058657   
3338   ('10107_197', '192.168.220.51')         71          0.010903   
5947   ('10361_244', '192.168.210.56')         42          0.063651   

       total_duration  total_packets  norm_latency  latency_rank  
1188            8.991            406      0.000039      0.002739  
10124          10.654            227      0.000046      0.002735  
105             8.979            241      0.000039      0.002735  
2818            9.810            128      0.000043      0.002732  
3338            8.835            654      0.000038      0.002729  
5947           14.919            132      0.000065      0.002726

### Count the frequency of each pair, above our 80th percentile rank, in the hour timestep

In [30]:
#Inner Merge in rankings to only keep pairs that pass the 80th percentile
df80=df.merge(pairs_count80[['pairs', 'frequency','latency_rank']], left_on='pairs2', right_on='pairs', how='inner')
df80=df80.drop('pairs_y', axis=1)
df80=df80.rename(columns={'pairs_x':'pairs'})
df80.head()#frequency and latency rank are for that pair, so in this df it will repeat b/c pairs repeat over time, norm_latency is for that individual timepoint

Unnamed: 0                     Date  Duration          Src_IP  Src_pt  \
0           0  2017-08-02 00:00:00.419     0.003  192.168.210.55   44870   
1           1  2017-08-02 00:00:00.421     0.000  192.168.100.11     445   
2          61  2017-08-02 00:01:00.581     0.000  192.168.100.11     445   
3          62  2017-08-02 00:01:00.580     0.000  192.168.210.55   44870   
4         126  2017-08-02 00:02:00.741     0.004  192.168.210.55   44870   

           Dst_IP   Dst_pt  Packets  Bytes                  date_hr  \
0  192.168.100.11    445.0        2    174  2017-08-02 00:00:00.000   
1  192.168.210.55  44870.0        1    108  2017-08-02 00:00:00.000   
2  192.168.210.55  44870.0        1    108  2017-08-02 00:00:00.000   
3  192.168.100.11    445.0        2    174  2017-08-02 00:00:00.000   
4  192.168.100.11    445.0        2    174  2017-08-02 00:00:00.000   

                                  pairs                                pairs2  \
0  ['192.168.100.11', '192.168.210.55']  ('192.168.100.11', '192.168.210.55')   
1  ['192.168.100.11', '192.168.210.55']  ('192.168.100.11', '192.168.210.55')   
2  ['192.168.100.11', '192.168.210.55']  ('192.168.100.11', '192.168.210.55')   
3  ['192.168.100.11', '192.168.210.55']  ('192.168.100.11', '192.168.210.55')   
4  ['192.168.100.11', '192.168.210.55']  ('192.168.100.11', '192.168.210.55')   

   norm_latency  frequency  latency_rank  
0        0.0015       1833      0.154555  
1        0.0000       1833      0.154555  
2        0.0000       1833      0.154555  
3        0.0000       1833      0.154555  
4        0.0020       1833      0.154555

In [34]:
df80.sort_values(by='pairs', ascending=False)

Unnamed: 0                     Date  Duration          Src_IP  Src_pt  \
254183      932527  2017-08-02 13:50:25.755     0.043  192.168.220.51   40951   
246880      722192  2017-08-02 12:23:12.195     0.003             DNS      53   
246932      723588  2017-08-02 12:24:05.418     0.004             DNS      53   
246931      723586  2017-08-02 12:24:05.365     0.001             DNS      53   
246930      723580  2017-08-02 12:24:05.424     0.002             DNS      53   
246929      723578  2017-08-02 12:24:05.425     0.000             DNS      53   
246928      723577  2017-08-02 12:24:05.415     0.000             DNS      53   
246927      723575  2017-08-02 12:24:05.418     0.000             DNS      53   
246926      723572  2017-08-02 12:24:05.060     0.002  192.168.220.51   46463   
246925      723569  2017-08-02 12:24:05.061     0.029  192.168.220.51   45761   
246924      723568  2017-08-02 12:24:05.061     0.041  192.168.220.51   49106   
246923      723567  2017-08-02 12:24:05.061     0.005  192.168.220.51   58570   
246922      723565  2017-08-02 12:24:05.060     0.002  192.168.220.51   45112   
246921      723564  2017-08-02 12:24:05.031     0.000  192.168.220.51   54511   
246920      723561  2017-08-02 12:24:05.102     0.004             DNS      53   
246919      723559  2017-08-02 12:24:05.087     0.018             DNS      53   
246918      723558  2017-08-02 12:24:05.061     0.005             DNS      53   
246933      723589  2017-08-02 12:24:05.414     0.000  192.168.220.51   53408   
246934      723591  2017-08-02 12:24:05.226     0.000  192.168.220.51   45614   
246935      723592  2017-08-02 12:24:05.417     0.000  192.168.220.51   33656   
246944      723618  2017-08-02 12:24:05.704     0.001             DNS      53   
246950      723634  2017-08-02 12:24:05.424     0.000  192.168.220.51   53573   
246949      723632  2017-08-02 12:24:05.678     0.000  192.168.220.51   55067   
246948      723631  2017-08-02 12:24:05.422     0.000  192.168.220.51   54285   
246947      723629  2017-08-02 12:24:05.676     0.000  192.168.220.51   36663   
246946      723623  2017-08-02 12:24:05.697     0.017             DNS      53   
246945      723622  2017-08-02 12:24:05.655     0.002             DNS      53   
246943      723617  2017-08-02 12:24:05.706     0.004             DNS      53   
246936      723594  2017-08-02 12:24:05.423     0.003  192.168.220.51   49816   
246942      723608  2017-08-02 12:24:05.697     0.000             DNS      53   
...            ...                      ...       ...             ...     ...   
718930      640879  2017-08-02 11:55:19.360     0.286  192.168.210.53   52565   
718931      641250  2017-08-02 11:55:25.272     0.000        10000_34     443   
718932      641280  2017-08-02 11:55:25.264     0.210  192.168.210.53   52546   
718933      641814  2017-08-02 11:55:31.646     0.320        10000_34     443   
718935      643791  2017-08-02 11:56:01.730     0.216  192.168.210.53   53080   
718936      643806  2017-08-02 11:56:01.748     0.000        10000_34     443   
718937      644464  2017-08-02 11:56:12.901     0.109        10000_34     443   
718919      636382  2017-08-02 11:54:26.983     0.000        10000_34     443   
718920      636412  2017-08-02 11:54:26.975     0.211  192.168.210.53   52546   
718905      629833  2017-08-02 11:52:41.067     1.251  192.168.210.53   52565   
718918      635848  2017-08-02 11:54:20.245     0.461        10000_34     443   
718917      635825  2017-08-02 11:54:20.228     0.422  192.168.210.53   52565   
718938      644481  2017-08-02 11:56:12.884     0.070  192.168.210.53   52565   
718940      644847  2017-08-02 11:56:17.548     0.000  192.168.210.53   53080   
718901      628919  2017-08-02 11:52:30.651     0.134  192.168.210.53   52546   
718902      628932  2017-08-02 11:52:30.661     0.173        10000_34     443   
718903      629222  2017-08-02 11:52:32.400     1.429        10000_34     443   
718904      629247  2017-08-02 11:52:32

In [35]:
#only care about those that passed 80th percent threshold
#count up how frequently each pair occurs in each hour timestep
df_hours=df80.groupby(['date_hr', 'pairs'],as_index=False)['Date'].count()
df_hours.head()

date_hr                            pairs  Date
0  2017-08-02 00:00:00.000  ['10001_213', '192.168.210.54']    53
1  2017-08-02 00:00:00.000  ['10002_162', '192.168.210.57']    10
2  2017-08-02 00:00:00.000  ['10002_174', '192.168.210.57']    30
3  2017-08-02 00:00:00.000  ['10003_235', '192.168.210.54']   214
4  2017-08-02 00:00:00.000  ['10004_250', '192.168.210.54']     6

In [36]:
df_hours['date_hr'].unique()

array(['2017-08-02 00:00:00.000', '2017-08-02 01:00:00.000',
       '2017-08-02 02:00:00.000', '2017-08-02 03:00:00.000',
       '2017-08-02 04:00:00.000', '2017-08-02 05:00:00.000',
       '2017-08-02 06:00:00.000', '2017-08-02 07:00:00.000',
       '2017-08-02 08:00:00.000', '2017-08-02 09:00:00.000',
       '2017-08-02 10:00:00.000', '2017-08-02 11:00:00.000',
       '2017-08-02 12:00:00.000', '2017-08-02 13:00:00.000',
       '2017-08-02 14:00:00.000'], dtype=object)

In [37]:
lDateColumn = 'date_hr'


In [39]:
df_hours= df_hours.groupby(["date_hr","pairs"])['Date'].sum().unstack(fill_value=0).reset_index().rename_axis(None, axis=1)

In [42]:
df_hours.head() #for the time series format

date_hr  ['10000_34', '192.168.210.53']  \
0  2017-08-02 00:00:00.000                               0   
1  2017-08-02 01:00:00.000                               0   
2  2017-08-02 02:00:00.000                               0   
3  2017-08-02 03:00:00.000                               0   
4  2017-08-02 04:00:00.000                               0   

   ['10000_34', '192.168.210.56']  ['10000_34', '192.168.220.47']  \
0                               0                               0   
1                               0                               0   
2                               0                               0   
3                               0                               0   
4                               0                               0   

   ['10000_34', '192.168.220.50']  ['10000_34', '192.168.220.51']  \
0                               0                               0   
1                               0                               0   
2                               0                               0   
3                               0                               0   
4                               0                               0   

   ['10000_66', '192.168.220.46']  ['10000_66', '192.168.220.47']  \
0                               0                               0   
1                               0                               0   
2                               0                               0   
3                               0                               0   
4                               0                               0   

   ['10000_66', '192.168.220.51']  ['10001_213', '192.168.210.54']  \
0                               0                               53   
1                               0                               72   
2                               0                               70   
3                               0                               82   
4                               0                               88   

             ...              ['192.168.210.57', 'DNS']  \
0            ...                                     16   
1            ...                                     28   
2            ...                                     32   
3            ...                                     44   
4            ...                                     32   

   ['192.168.220.42', 'DNS']  ['192.168.220.43', 'DNS']  \
0                          0                          0   
1                          0                          0   
2                          0                          0   
3                          0                          0   
4                          0                          0   

   ['192.168.220.45', 'DNS']  ['192.168.220.46', 'DNS']  \
0                          0                          0   
1                          0                          0   
2                          0                          0   
3                          0                          0   
4                          0                          0   

   ['192.168.220.47', 'DNS']  ['192.168.220.48', 'DNS']  \
0                          0                          0   
1                          0                          0   
2                          0                          0   
3                          0                          0   
4                          0                          0   

   ['192.168.220.49', 'DNS']  ['192.168.220.50', 'DNS']  \
0                          0                          0   
1                          0                          0   
2                          0                          0   
3                          0                          0   
4                          0                          0   

   ['192.168.220.51', 'DNS']  
0                          0  
1                          0  
2                          0  
3                          0  
4                          0  

[5 rows x 2133 col

In [43]:
CN_columns = [col for col in French_Wine_Export_in_Euros_DF.columns if col.endswith('_CN') ]
French_Wine_Export_in_Euros_DF[CN_columns].describe()

ALSACE_BLANC_CN  BEAUJOLAIS_ROUGE_CN  BORDEAUX_BLANC_CN  \
count        50.000000             50.00000       5.000000e+01   
mean     119348.360000         130292.47000       4.993186e+05   
std       65116.609016         102214.45714       2.936971e+05   
min       19546.000000           5833.00000       1.678740e+05   
25%       82278.500000          66206.50000       3.117738e+05   
50%       98656.000000          98427.50000       4.148980e+05   
75%      161694.000000         158673.75000       5.623658e+05   
max      317661.000000         453985.00000       1.890312e+06   

       BORDEAUX_ROUGE_CN  BOURGOGNE_BLANC_CN  BOURGOGNE_ROUGE_CN  \
count       5.000000e+01           50.000000        5.000000e+01   
mean        1.138432e+07       242575.340000        7.436432e+05   
std         3.081051e+06        99492.736867        4.176045e+05   
min         5.377235e+06        75396.000000        2.725460e+05   
25%         9.737536e+06       171633.250000        4.214805e+05   
50%         1.039686e+07       237099.500000        6.060540e+05   
75%         1.316721e+07       308119.750000        9.648268e+05   
max         1.905088e+07       535157.000000        2.021852e+06   

       CHAMPAGNE_MOUSSEUX_CN  EUROPE_ROUGE_CN  FRANCE_BLANC_CN  \
count           5.000000e+01     5.000000e+01        50.000000   
mean            6.225160e+05     8.313372e+05     12978.062000   
std             3.812781e+05     2.337996e+05     24705.479992   
min             1.976760e+05     3.270090e+05         0.000000   
25%             3.897600e+05     6.529608e+05      1607.250000   
50%             5.299100e+05     8.078685e+05      6237.750000   
75%             7.029695e+05     9.859902e+05     14842.000000   
max             2.103130e+06     1.367882e+06    163701.000000   

       FRANCE_MOUSSEUX_CN  FRANCE_ROUGE_CN  LANGUEDOC_ROUGE_CN  \
count           50.000000        50.000000        5.000000e+01   
mean         93298.256667     11185.281403        1.304245e+06   
std          63521.773261     13888.069451        6.352887e+05   
min          20488.500000       260.500000        4.916860e+05   
25%          46355.750000      4759.017857        9.207640e+05   
50%          82644.583333      8837.333333        1.211934e+06   
75%         118693.250000     12869.584821        1.416010e+06   
max         366064.500000     96564.222222        3.607517e+06   

       LOIRE_BLANC_CN  LOIRE_ROUGE_CN  OTHER_ROUGE_CN  RHÔNE_ROUGE_CN  
count       50.000000       50.000000       50.000000    5.000000e+01  
mean     48771.330000    92016.740000    52969.948000    7.498312e+05  
std      27922.200988    54704.609614    36129.014739    3.592653e+05  
min      16643.500000    15325.000000     6337.750000    1.888270e+05  
25%      31191.250000    54588.250000    28779.650000    5.089532e+05  
50%      37845.750000    77491.500000    44118.875000    7.065070e+05  
75%      62140.375000   119915.500000    62176.000000    9.285735e+05  
max     151128.000000   272948.000000   179114.750000    1.755449e+06

In [44]:
CN_columns

['ALSACE_BLANC_CN',
 'BEAUJOLAIS_ROUGE_CN',
 'BORDEAUX_BLANC_CN',
 'BORDEAUX_ROUGE_CN',
 'BOURGOGNE_BLANC_CN',
 'BOURGOGNE_ROUGE_CN',
 'CHAMPAGNE_MOUSSEUX_CN',
 'EUROPE_ROUGE_CN',
 'FRANCE_BLANC_CN',
 'FRANCE_MOUSSEUX_CN',
 'FRANCE_ROUGE_CN',
 'LANGUEDOC_ROUGE_CN',
 'LOIRE_BLANC_CN',
 'LOIRE_ROUGE_CN',
 'OTHER_ROUGE_CN',
 'RHÔNE_ROUGE_CN']

In [45]:
Wines = "ALSACE BEAUJOLAIS BORDEAUX BOURGOGNE CHAMPAGNE EUROPE FRANCE LANGUEDOC LOIRE OTHER RHÔNE".split();
Variants = ['BLANC' , 'MOUSSEUX' , 'ROUGE'];
Countries = ['GB', 'US', 'DE', 'BE', 'CN', 'JP', 'CH', 'HK', 'NL', 'CA' , 'OTHER']

In [10]:
Variants

['BLANC', 'MOUSSEUX', 'ROUGE']


## Grouping Definition

In [50]:
pairs = list(df80['pairs'].unique()) #unique pairs are the groups
#lDict = dict(pairs)


In [51]:
# Grouping definition
lGroups = {}
lGroups["pairs"] = pairs

lHierarchy = {};
lHierarchy['Levels'] = None;
lHierarchy['Data'] = None;
lHierarchy['Groups']= lGroups;
# the most important !!!!
lHierarchy['GroupOrder']= ["pairs"]; # group by Wine first, then by variant, etc
lHierarchy['Type'] = "Grouped";

In [52]:

lHierarchy

{'Levels': None,
 'Data': None,
 'Groups': {'pairs': ["['192.168.100.11', '192.168.210.55']",
   "['192.168.100.11', '192.168.220.47']",
   "['192.168.100.11', '192.168.220.42']",
   "['192.168.100.11', '192.168.220.46']",
   "['192.168.100.11', '192.168.210.46']",
   "['192.168.100.11', '192.168.220.43']",
   "['192.168.100.11', '192.168.220.44']",
   "['192.168.100.11', '192.168.210.50']",
   "['192.168.100.11', '192.168.220.48']",
   "['192.168.100.11', '192.168.210.56']",
   "['10001_213', '192.168.210.54']",
   "['192.168.100.11', '192.168.210.45']",
   "['192.168.100.11', '192.168.220.50']",
   "['192.168.100.11', '192.168.210.47']",
   "['192.168.100.11', '192.168.210.48']",
   "['192.168.100.11', '192.168.220.49']",
   "['192.168.100.11', '192.168.210.49']",
   "['192.168.100.11', '192.168.220.45']",
   "['192.168.100.11', '192.168.220.51']",
   "['10003_235', '192.168.210.54']",
   "['10004_250', '192.168.210.57']",
   "['10004_250', '192.168.210.54']",
   "['192.168.210.255',

In [53]:
import pyaf.HierarchicalForecastEngine as hautof
lEngine = hautof.cHierarchicalForecastEngine()


#lSignalHierarchy = lEngine.plot_Hierarchy(French_Wine_Export_in_Euros_DF , "Month", "Signal", 1, 
                                    #      lHierarchy, None);

## Hierarchical Modelling

In [54]:
# create a hierarchical model and train it
import pyaf.HierarchicalForecastEngine as hautof

lEngine = hautof.cHierarchicalForecastEngine()

lSignalVar = "frequency";

#remove some data so we can train
N = df_hours.shape[0];
H = 3;
train_df = df_hours.head(N-H);


In [55]:
train_df['date_hr']=pd.to_datetime(train_df['date_hr'], format="%Y-%m-%d %H:%M:%S.%f", errors = 'coerce')

/home/ubuntu/anaconda3/lib/python3.6/site-packages/ipykernel/__main__.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  if __name__ == '__main__':


In [56]:
train_df.tail()

date_hr  ['10000_34', '192.168.210.53']  \
7  2017-08-02 07:00:00                               0   
8  2017-08-02 08:00:00                               0   
9  2017-08-02 09:00:00                               0   
10 2017-08-02 10:00:00                               0   
11 2017-08-02 11:00:00                               0   

    ['10000_34', '192.168.210.56']  ['10000_34', '192.168.220.47']  \
7                                0                               8   
8                                0                               0   
9                                0                               0   
10                              94                               0   
11                               0                             119   

    ['10000_34', '192.168.220.50']  ['10000_34', '192.168.220.51']  \
7                                0                               0   
8                                0                               0   
9                                0                               0   
10                               0                               0   
11                              71                               0   

    ['10000_66', '192.168.220.46']  ['10000_66', '192.168.220.47']  \
7                                8                               0   
8                                0                              31   
9                                0                              52   
10                               0                               0   
11                              18                               0   

    ['10000_66', '192.168.220.51']  ['10001_213', '192.168.210.54']  \
7                                0                              184   
8                                0                              146   
9                                0                                0   
10                               0                                0   
11                               0                                0   

              ...              ['192.168.210.57', 'DNS']  \
7             ...                                     36   
8             ...                                     28   
9             ...                                      0   
10            ...                                     24   
11            ...                                      4   

    ['192.168.220.42', 'DNS']  ['192.168.220.43', 'DNS']  \
7                           0                         81   
8                           0                         56   
9                         979                         14   
10                        142                          0   
11                       2264                          0   

    ['192.168.220.45', 'DNS']  ['192.168.220.46', 'DNS']  \
7                           0                        776   
8                           0                          0   
9                        1542                         12   
10                       1468                          0   
11                         94                        222   

    ['192.168.220.47', 'DNS']  ['192.168.220.48', 'DNS']  \
7                        2835                          0   
8                        5661                        113   
9                        6330                       1439   
10                       2318                          0   
11                       3954                       1501   

    ['192.168.220.49', 'DNS']  ['192.168.220.50', 'DNS']  \
7                           0                          0   
8                           0                          0   
9                         158                          0   
10                       2957                       1656   
11                         36                       3396   

    ['192.168.220.51', 'DNS']  
7                           0  
8                           2  
9                         332  
10                          0  
11         

In [57]:
lSignalHierarchy = lEngine.train(train_df , lDateColumn, lSignalVar, 1, lHierarchy, None);

INFO:pyaf.std:START_HIERARCHICAL_TRAINING
INFO:pyaf.hierarchical:TRAINING_MODEL_LEVEL_SIGNAL 0 ['10000_34', '192.168.210.53']
INFO:pyaf.std:START_TRAINING '['10000_34', '192.168.210.53']'
INFO:pyaf.std:END_TRAINING_TIME_IN_SECONDS '['10000_34', '192.168.210.53']' 0.7928295135498047
INFO:pyaf.std:TIME_DETAIL TimeVariable='date_hr' TimeMin=2017-08-02T00:00:00.000000 TimeMax=2017-08-02T11:00:00.000000 TimeDelta=<DateOffset: hours=1> Horizon=1
INFO:pyaf.std:SIGNAL_DETAIL_ORIG SignalVariable='['10000_34', '192.168.210.53']' Min=0 Max=0  Mean=0.0 StdDev=0.0
INFO:pyaf.std:SIGNAL_DETAIL_TRANSFORMED TransformedSignalVariable='_['10000_34', '192.168.210.53']' Min=0 Max=0  Mean=0.0 StdDev=0.0
INFO:pyaf.std:BEST_TRANSOFORMATION_TYPE '_'
INFO:pyaf.std:BEST_DECOMPOSITION  '_['10000_34', '192.168.210.53']_ConstantTrend_residue_zeroCycle_residue_NoAR' [ConstantTrend + NoCycle + NoAR]
INFO:pyaf.std:TREND_DETAIL '_['10000_34', '192.168.210.53']_ConstantTrend' [ConstantTrend]
INFO:pyaf.std:CYCLE_DETAIL '

INFO:pyaf.std:MODEL_MAPE MAPE_Fit=0.0 MAPE_Forecast=0.0 MAPE_Test=0.0
INFO:pyaf.std:MODEL_SMAPE SMAPE_Fit=0.0 SMAPE_Forecast=0.0 SMAPE_Test=0.0
INFO:pyaf.std:MODEL_MASE MASE_Fit=0.0 MASE_Forecast=0.0 MASE_Test=0.0
INFO:pyaf.std:MODEL_L1 L1_Fit=0.0 L1_Forecast=0.0 L1_Test=0.0
INFO:pyaf.std:MODEL_L2 L2_Fit=0.0 L2_Forecast=0.0 L2_Test=0.0
INFO:pyaf.std:MODEL_COMPLEXITY 0
INFO:pyaf.std:AR_MODEL_DETAIL_START
INFO:pyaf.std:AR_MODEL_DETAIL_END
INFO:pyaf.hierarchical:TRAINING_MODEL_LEVEL_SIGNAL 0 ['10000_66', '192.168.220.46']
INFO:pyaf.std:START_TRAINING '['10000_66', '192.168.220.46']'
INFO:pyaf.std:END_TRAINING_TIME_IN_SECONDS '['10000_66', '192.168.220.46']' 0.5235488414764404
INFO:pyaf.std:TIME_DETAIL TimeVariable='date_hr' TimeMin=2017-08-02T00:00:00.000000 TimeMax=2017-08-02T11:00:00.000000 TimeDelta=<DateOffset: hours=1> Horizon=1
INFO:pyaf.std:SIGNAL_DETAIL_ORIG SignalVariable='['10000_66', '192.168.220.46']' Min=0 Max=54  Mean=6.666666666666667 StdDev=15.195028426721974
INFO:pyaf.std

INFO:pyaf.std:TREND_DETAIL 'Diff_['10001_213', '192.168.210.55']_ConstantTrend' [ConstantTrend]
INFO:pyaf.std:CYCLE_DETAIL 'Diff_['10001_213', '192.168.210.55']_ConstantTrend_residue_zeroCycle' [NoCycle]
INFO:pyaf.std:AUTOREG_DETAIL 'Diff_['10001_213', '192.168.210.55']_ConstantTrend_residue_zeroCycle_residue_NoAR' [NoAR]
INFO:pyaf.std:MODEL_MAPE MAPE_Fit=0.1667 MAPE_Forecast=0.1667 MAPE_Test=0.1667
INFO:pyaf.std:MODEL_SMAPE SMAPE_Fit=0.3333 SMAPE_Forecast=0.3333 SMAPE_Test=0.3333
INFO:pyaf.std:MODEL_MASE MASE_Fit=0.88 MASE_Forecast=0.88 MASE_Test=0.88
INFO:pyaf.std:MODEL_L1 L1_Fit=16.0 L1_Forecast=16.0 L1_Test=16.0
INFO:pyaf.std:MODEL_L2 L2_Fit=39.22584182228174 L2_Forecast=39.22584182228174 L2_Test=39.22584182228174
INFO:pyaf.std:MODEL_COMPLEXITY 32
INFO:pyaf.std:AR_MODEL_DETAIL_START
INFO:pyaf.std:AR_MODEL_DETAIL_END
INFO:pyaf.hierarchical:TRAINING_MODEL_LEVEL_SIGNAL 0 ['10001_213', '192.168.220.45']
INFO:pyaf.std:START_TRAINING '['10001_213', '192.168.220.45']'
INFO:pyaf.std:END_TR

INFO:pyaf.std:SIGNAL_DETAIL_ORIG SignalVariable='['10002_1', '192.168.210.55']' Min=0 Max=138  Mean=22.666666666666668 StdDev=42.94440850939994
INFO:pyaf.std:SIGNAL_DETAIL_TRANSFORMED TransformedSignalVariable='Diff_['10002_1', '192.168.210.55']' Min=-88.0 Max=130.0  Mean=0.0 StdDev=49.57149718672348
INFO:pyaf.std:BEST_TRANSOFORMATION_TYPE 'Diff_'
INFO:pyaf.std:BEST_DECOMPOSITION  'Diff_['10002_1', '192.168.210.55']_ConstantTrend_residue_zeroCycle_residue_NoAR' [ConstantTrend + NoCycle + NoAR]
INFO:pyaf.std:TREND_DETAIL 'Diff_['10002_1', '192.168.210.55']_ConstantTrend' [ConstantTrend]
INFO:pyaf.std:CYCLE_DETAIL 'Diff_['10002_1', '192.168.210.55']_ConstantTrend_residue_zeroCycle' [NoCycle]
INFO:pyaf.std:AUTOREG_DETAIL 'Diff_['10002_1', '192.168.210.55']_ConstantTrend_residue_zeroCycle_residue_NoAR' [NoAR]
INFO:pyaf.std:MODEL_MAPE MAPE_Fit=0.3333 MAPE_Forecast=0.3333 MAPE_Test=0.3333
INFO:pyaf.std:MODEL_SMAPE SMAPE_Fit=0.6667 SMAPE_Forecast=0.6667 SMAPE_Test=0.6667
INFO:pyaf.std:MODEL_M

INFO:pyaf.std:AR_MODEL_DETAIL_START
INFO:pyaf.std:AR_MODEL_DETAIL_END
INFO:pyaf.hierarchical:TRAINING_MODEL_LEVEL_SIGNAL 0 ['10002_1', '192.168.220.50']
INFO:pyaf.std:START_TRAINING '['10002_1', '192.168.220.50']'
INFO:pyaf.std:END_TRAINING_TIME_IN_SECONDS '['10002_1', '192.168.220.50']' 0.7391178607940674
INFO:pyaf.std:TIME_DETAIL TimeVariable='date_hr' TimeMin=2017-08-02T00:00:00.000000 TimeMax=2017-08-02T11:00:00.000000 TimeDelta=<DateOffset: hours=1> Horizon=1
INFO:pyaf.std:SIGNAL_DETAIL_ORIG SignalVariable='['10002_1', '192.168.220.50']' Min=0 Max=89  Mean=7.416666666666667 StdDev=24.598300528469213
INFO:pyaf.std:SIGNAL_DETAIL_TRANSFORMED TransformedSignalVariable='Diff_['10002_1', '192.168.220.50']' Min=-89.0 Max=89.0  Mean=0.0 StdDev=36.33409785128381
INFO:pyaf.std:BEST_TRANSOFORMATION_TYPE 'Diff_'
INFO:pyaf.std:BEST_DECOMPOSITION  'Diff_['10002_1', '192.168.220.50']_ConstantTrend_residue_zeroCycle_residue_NoAR' [ConstantTrend + NoCycle + NoAR]
INFO:pyaf.std:TREND_DETAIL 'Diff_[

...

INFO:pyaf.std:REPORT_COMBINED_FORECASTS_VALID_PERF ("['10308_169', '192.168.220.47']_BU", 15.01110699893027, 0.0833, 15.01110699893027, 0.0833)
INFO:pyaf.std:REPORT_COMBINED_FORECASTS_FIT_PERF ("['10309_173', '192.168.220.47']_BU", 9.1104335791443, 0.1852, 9.1104335791443, 0.1852)
INFO:pyaf.std:REPORT_COMBINED_FORECASTS_VALID_PERF ("['10309_173', '192.168.220.47']_BU", 9.1104335791443, 0.1852, 9.1104335791443, 0.1852)
INFO:pyaf.std:REPORT_COMBINED_FORECASTS_FIT_PERF ("['10310_43', '192.168.220.45']_BU", 0.0, 0.0, 0.0, 0.0)
INFO:pyaf.std:REPORT_COMBINED_FORECASTS_VALID_PERF ("['10310_43', '192.168.220.45']_BU", 0.0, 0.0, 0.0, 0.0)
INFO:pyaf.std:REPORT_COMBINED_FORECASTS_FIT_PERF ("['10311_172', '192.168.220.49']_BU", 11.258330249197702, 0.0833, 11.258330249197702, 0.0833)
INFO:pyaf.std:REPORT_COMBINED_FORECASTS_VALID_PERF ("['10311_172', '192.168.220.49']_BU", 11.258330249197702, 0.0833, 11.258330249197702, 0.0833)
INFO:pyaf.std:REPORT_COMBINED_FORECASTS_FIT_PERF ("['10311_55', '192.168

INFO:pyaf.std:REPORT_COMBINED_FORECASTS_VALID_PERF ("['10321_4', '192.168.210.46']_BU", 0.0, 0.0, 0.0, 0.0)
INFO:pyaf.std:REPORT_COMBINED_FORECASTS_FIT_PERF ("['10321_4', '192.168.210.53']_BU", 0.0, 0.0, 0.0, 0.0)
INFO:pyaf.std:REPORT_COMBINED_FORECASTS_VALID_PERF ("['10321_4', '192.168.210.53']_BU", 0.0, 0.0, 0.0, 0.0)
INFO:pyaf.std:REPORT_COMBINED_FORECASTS_FIT_PERF ("['10321_4', '192.168.210.56']_BU", 0.0, 0.0, 0.0, 0.0)
INFO:pyaf.std:REPORT_COMBINED_FORECASTS_VALID_PERF ("['10321_4', '192.168.210.56']_BU", 0.0, 0.0, 0.0, 0.0)
INFO:pyaf.std:REPORT_COMBINED_FORECASTS_FIT_PERF ("['10321_4', '192.168.210.57']_BU", 0.0, 0.0, 0.0, 0.0)
INFO:pyaf.std:REPORT_COMBINED_FORECASTS_VALID_PERF ("['10321_4', '192.168.210.57']_BU", 0.0, 0.0, 0.0, 0.0)
INFO:pyaf.std:REPORT_COMBINED_FORECASTS_FIT_PERF ("['10321_4', '192.168.220.42']_BU", 40.414518843273804, 0.0833, 40.414518843273804, 0.0833)
INFO:pyaf.std:REPORT_COMBINED_FORECASTS_VALID_PERF ("['10321_4', '192.168.220.42']_BU", 40.414518843273804, 

INFO:pyaf.std:REPORT_COMBINED_FORECASTS_FIT_PERF ("['10323_87', '192.168.220.47']_BU", 72.52872993970504, 0.25, 72.52872993970504, 0.25)
INFO:pyaf.std:REPORT_COMBINED_FORECASTS_VALID_PERF ("['10323_87', '192.168.220.47']_BU", 72.52872993970504, 0.25, 72.52872993970504, 0.25)
INFO:pyaf.std:REPORT_COMBINED_FORECASTS_FIT_PERF ("['10323_87', '192.168.220.48']_BU", 51.67284909247151, 0.0833, 51.67284909247151, 0.0833)
INFO:pyaf.std:REPORT_COMBINED_FORECASTS_VALID_PERF ("['10323_87', '192.168.220.48']_BU", 51.67284909247151, 0.0833, 51.67284909247151, 0.0833)
INFO:pyaf.std:REPORT_COMBINED_FORECASTS_FIT_PERF ("['10323_87', '192.168.220.49']_BU", 58.601052322747016, 0.0833, 58.601052322747016, 0.0833)
INFO:pyaf.std:REPORT_COMBINED_FORECASTS_VALID_PERF ("['10323_87', '192.168.220.49']_BU", 58.601052322747016, 0.0833, 58.601052322747016, 0.0833)
INFO:pyaf.std:REPORT_COMBINED_FORECASTS_FIT_PERF ("['10323_87', '192.168.220.51']_BU", 18.76388374866284, 0.0833, 18.76388374866284, 0.0833)
INFO:pyaf.s

INFO:pyaf.std:REPORT_COMBINED_FORECASTS_FIT_PERF ("['10339_42', '192.168.210.55']_BU", 0.0, 0.0, 0.0, 0.0)
INFO:pyaf.std:REPORT_COMBINED_FORECASTS_VALID_PERF ("['10339_42', '192.168.210.55']_BU", 0.0, 0.0, 0.0, 0.0)
INFO:pyaf.std:REPORT_COMBINED_FORECASTS_FIT_PERF ("['10339_42', '192.168.220.49']_BU", 0.0, 0.0, 0.0, 0.0)
INFO:pyaf.std:REPORT_COMBINED_FORECASTS_VALID_PERF ("['10339_42', '192.168.220.49']_BU", 0.0, 0.0, 0.0, 0.0)
INFO:pyaf.std:REPORT_COMBINED_FORECASTS_FIT_PERF ("['10339_43', '192.168.220.49']_BU", 6.928203230275509, 0.0833, 6.928203230275509, 0.0833)
INFO:pyaf.std:REPORT_COMBINED_FORECASTS_VALID_PERF ("['10339_43', '192.168.220.49']_BU", 6.928203230275509, 0.0833, 6.928203230275509, 0.0833)
INFO:pyaf.std:REPORT_COMBINED_FORECASTS_FIT_PERF ("['10340_122', '192.168.210.55']_BU", 49.33220719435394, 0.1667, 49.33220719435394, 0.1667)
INFO:pyaf.std:REPORT_COMBINED_FORECASTS_VALID_PERF ("['10340_122', '192.168.210.55']_BU", 49.33220719435394, 0.1667, 49.33220719435394, 0.1667

INFO:pyaf.std:REPORT_COMBINED_FORECASTS_FIT_PERF ("['192.168.210.53', 'DNS']_BU", 36.157064777624484, 0.9167, 36.157064777624484, 0.9167)
INFO:pyaf.std:REPORT_COMBINED_FORECASTS_VALID_PERF ("['192.168.210.53', 'DNS']_BU", 36.157064777624484, 0.9167, 36.157064777624484, 0.9167)
INFO:pyaf.std:REPORT_COMBINED_FORECASTS_FIT_PERF ("['192.168.210.55', 'DNS']_BU", 1375.0107272308824, 0.4167, 1375.0107272308824, 0.4167)
INFO:pyaf.std:REPORT_COMBINED_FORECASTS_VALID_PERF ("['192.168.210.55', 'DNS']_BU", 1375.0107272308824, 0.4167, 1375.0107272308824, 0.4167)
INFO:pyaf.std:REPORT_COMBINED_FORECASTS_FIT_PERF ("['192.168.210.56', 'DNS']_BU", 840.0813452676274, 0.1667, 840.0813452676274, 0.1667)
INFO:pyaf.std:REPORT_COMBINED_FORECASTS_VALID_PERF ("['192.168.210.56', 'DNS']_BU", 840.0813452676274, 0.1667, 840.0813452676274, 0.1667)
INFO:pyaf.std:REPORT_COMBINED_FORECASTS_FIT_PERF ("['192.168.210.57', 'DNS']_BU", 54.78374995616181, 1.691, 54.78374995616181, 1.691)
INFO:pyaf.std:REPORT_COMBINED_FORECA

In [58]:
lInfo = lEngine.to_json()
lInfo.keys()

dict_keys(['Structure', 'Models'])

In [59]:
lInfo['Models'].keys()

dict_keys(["['10000_34', '192.168.210.53']", "['10000_34', '192.168.210.56']", "['10000_34', '192.168.220.47']", "['10000_34', '192.168.220.50']", "['10000_34', '192.168.220.51']", "['10000_66', '192.168.220.46']", "['10000_66', '192.168.220.47']", "['10000_66', '192.168.220.51']", "['10001_213', '192.168.210.54']", "['10001_213', '192.168.210.55']", "['10001_213', '192.168.220.45']", "['10001_213', '192.168.220.50']", "['10001_213', '192.168.220.51']", "['10002_1', '192.168.210.46']", "['10002_1', '192.168.210.55']", "['10002_1', '192.168.210.56']", "['10002_1', '192.168.220.45']", "['10002_1', '192.168.220.46']", "['10002_1', '192.168.220.47']", "['10002_1', '192.168.220.50']", "['10002_10', '192.168.210.55']", "['10002_10', '192.168.210.56']", "['10002_10', '192.168.220.47']", "['10002_10', '192.168.220.50']", "['10002_14', '192.168.210.45']", "['10002_14', '192.168.210.46']", "['10002_14', '192.168.210.48']", "['10002_14', '192.168.210.50']", "['10002_14', '192.168.210.54']", "['10

In [60]:
H=3
dfapp_out = lEngine.forecast(train_df, H) #H is the number of timesteps to predict out, like 12=12 months

INFO:pyaf.std:START_HIERARCHICAL_FORECASTING
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8740301132202148
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8566694259643555
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.843472957611084
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8442292213439941
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8604686260223389
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8576548099517822
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8454103469848633
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8533995151519775
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8649759292602539
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8389265537261963
INFO:pyaf.std:ST

INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8454709053039551
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.845750093460083
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8556909561157227
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8529319763183594
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.84187912940979
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8725306987762451
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8732192516326904
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8474631309509277
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8582079410552979
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8429660797119141
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME

INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8662114143371582
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8560984134674072
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8628659248352051
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8551731109619141
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8562994003295898
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8603622913360596
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8550615310668945
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8637609481811523
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.855003833770752
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8582665920257568
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.859804630279541


INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8891181945800781
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8717284202575684
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8626716136932373
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8582541942596436
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8646872043609619
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8710291385650635
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8470048904418945
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8593556880950928
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.85614013671875
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8760499954223633
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIM

INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8468148708343506
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8562984466552734
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8544955253601074
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8562843799591064
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8454856872558594
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.855478048324585
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.843491792678833
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8396129608154297
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.865048885345459
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8578832149505615
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8537874221801758
I

...

INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8735063076019287
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8631787300109863
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.87872314453125
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8593893051147461
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8508453369140625
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8663344383239746
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8634805679321289
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8504078388214111
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8516545295715332
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8727419376373291
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIM

INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8656365871429443
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8769309520721436
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8466460704803467
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8680038452148438
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8577923774719238
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8410840034484863
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8464958667755127
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8569872379302979
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8557548522949219
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8444521427154541
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.882439374923706

INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8749814033508301
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.877652645111084
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8645379543304443
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8735041618347168
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8851501941680908
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8848745822906494
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8667027950286865
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8860683441162109
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.873314380645752
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8711535930633545
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIM

INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.9184021949768066
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8957512378692627
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8904571533203125
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8956789970397949
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.9174532890319824
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8680596351623535
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8600871562957764
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8508181571960449
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8716368675231934
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8671412467956543
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.851294755935669

INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8672411441802979
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8494281768798828
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.849536657333374
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8687193393707275
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8647894859313965
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8740851879119873
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8596310615539551
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8698370456695557
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8635349273681641
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TIME_IN_SECONDS 0.8679404258728027
INFO:pyaf.std:START_FORECASTING
INFO:pyaf.std:END_FORECAST_TI